In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/netflix-prize-data/combined_data_3.txt
/kaggle/input/netflix-prize-data/movie_titles.csv
/kaggle/input/netflix-prize-data/combined_data_4.txt
/kaggle/input/netflix-prize-data/combined_data_1.txt
/kaggle/input/netflix-prize-data/README
/kaggle/input/netflix-prize-data/probe.txt
/kaggle/input/netflix-prize-data/combined_data_2.txt
/kaggle/input/netflix-prize-data/qualifying.txt


In [2]:
# Read combined_data files
read_data = pd.read_csv("../input/netflix-prize-data/combined_data_1.txt",header=None, names=['Cust_Id', 'Rating', 'Date_Rt'], usecols=[0, 1, 2])
#read_data = read_data.append(pd.read_csv("../input/netflix-prize-data/combined_data_2.txt",header=None, names=['Cust_Id', 'Rating', 'Date_Rt'], usecols=[0, 1, 2]))
#read_data = read_data.append(pd.read_csv("../input/netflix-prize-data/combined_data_3.txt",header=None, names=['Cust_Id', 'Rating', 'Date_Rt'], usecols=[0, 1, 2]))
#read_data = read_data.append(pd.read_csv("../input/netflix-prize-data/combined_data_4.txt",header=None, names=['Cust_Id', 'Rating', 'Date_Rt'], usecols=[0, 1, 2]))

read_data

Cust_Id  Rating     Date_Rt
0              1:     NaN         NaN
1         1488844     3.0  2005-09-06
2          822109     5.0  2005-05-13
3          885013     4.0  2005-10-19
4           30878     4.0  2005-12-26
...           ...     ...         ...
24058258  2591364     2.0  2005-02-16
24058259  1791000     2.0  2005-02-10
24058260   512536     5.0  2005-07-27
24058261   988963     3.0  2005-12-20
24058262  1704416     3.0  2004-06-02

[24058263 rows x 3 columns]

In [3]:
# Create  movie ID column and past movie ID
read_data["Movie_Id"] = read_data["Cust_Id"].apply(lambda x: x if ":" in x else np.nan)
read_data["Movie_Id"] = read_data["Movie_Id"].str.replace(":","")
#Fill nan values with precendant not nan value
read_data["Movie_Id"]=read_data["Movie_Id"].fillna(method="ffill")
read_data = read_data.dropna()

read_data

Cust_Id  Rating     Date_Rt Movie_Id
1         1488844     3.0  2005-09-06        1
2          822109     5.0  2005-05-13        1
3          885013     4.0  2005-10-19        1
4           30878     4.0  2005-12-26        1
5          823519     3.0  2004-05-03        1
...           ...     ...         ...      ...
24058258  2591364     2.0  2005-02-16     4499
24058259  1791000     2.0  2005-02-10     4499
24058260   512536     5.0  2005-07-27     4499
24058261   988963     3.0  2005-12-20     4499
24058262  1704416     3.0  2004-06-02     4499

[24053764 rows x 4 columns]

In [4]:
read_data['Cust_Id'] = read_data['Cust_Id'].astype(int)
read_data['Rating'] = read_data['Rating'].astype(int)
read_data['Movie_Id'] = read_data['Movie_Id'].astype(int)
#read_data['Date_Rt'] = read_data['Date_Rt'].astype('datetime64')
read_data.dtypes

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documen

Cust_Id      int64
Rating       int64
Date_Rt     object
Movie_Id     int64
dtype: object

In [5]:
#movie_titles = pd.read_csv("../input/netflix-prize-data/movie_titles.csv", encoding = "ISO-8859-1", header=None, names=['Movie_Id', 'Year', 'Title'], usecols=[0, 1, 2])
#movie_titles

In [6]:
# To create interactive plots
from plotly.offline import init_notebook_mode, plot, iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)

# Get data
data = read_data['Rating'].value_counts().sort_index(ascending=False)

# Create trace
trace = go.Bar(x = data.index,
               text = ['{:.1f} %'.format(val) for val in (data.values / read_data.shape[0] * 100)],
               textposition = 'auto',
               textfont = dict(color = '#000000'),
               y = data.values,
               marker = dict(color = '#0054db'))
# Create layout
layout = dict(title = 'Distribution Of {} Netflix-Ratings'.format(read_data.shape[0]),
              xaxis = dict(title = 'Rating'),
              yaxis = dict(title = 'Count'))
# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [7]:
print(read_data.groupby('Cust_Id')['Rating'].count().sort_values(ascending=False))#num of ratings per user

Cust_Id
305344     4467
387418     4422
2439493    4195
1664010    4019
2118461    3769
           ... 
1605874       1
2429614       1
1605861       1
960296        1
1100658       1
Name: Rating, Length: 470758, dtype: int64


In [8]:
##### Ratings Per User #####
# Get data
data = read_data.groupby('Cust_Id')['Rating'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(size = 20),
                     marker = dict(color = '#0054db'))
# Create layout
layout = go.Layout(title = 'Distribution Of Ratings Per User {} Netflix-Ratings'.format(read_data.shape[0]),
                   xaxis = dict(title = 'Ratings Per User'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [9]:
print(read_data.groupby('Movie_Id')['Rating'].count().sort_values(ascending=False))#num of ratings per user

Movie_Id
1905    193941
2152    162597
3860    160454
4432    156183
571     154832
         ...  
4294        44
915         43
3656        42
4338        39
4362        36
Name: Rating, Length: 4499, dtype: int64


In [10]:
##### Ratings Per Movie #####
# Get data
data = read_data.groupby('Movie_Id')['Rating'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(size = 500),
                     marker = dict(color = '#0054db'))
# Create layout
layout = go.Layout(title = 'Distribution Of Ratings Per Movie {} Netflix-Ratings'.format(read_data.shape[0]),
                   xaxis = dict(title = 'Ratings Per Movie'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [11]:
# Filter sparse users in read_data
min_user_ratings = 200
filter_users = (read_data['Cust_Id'].value_counts()>=min_user_ratings)
filter_users = filter_users[filter_users].index.tolist()
User_filterd = read_data[(read_data['Cust_Id'].isin(filter_users))]
print('After fitering Users:\t{}'.format(User_filterd.shape))

# Filter sparse movies in read_data
min_movie_ratings = 300 #need to go up to 10000 movies to afect yhe dataset
filter_movies = (User_filterd['Movie_Id'].value_counts()>=min_movie_ratings)
filter_movies = filter_movies[filter_movies].index.tolist()
User_filterd = User_filterd[(User_filterd['Movie_Id'].isin(filter_movies))]
print('After fitering Movies:\t{}'.format(User_filterd.shape))

# Actual filtering
#User_filterd = read_data[(read_data['Movie_Id'].isin(filter_movies)) & (read_data['Cust_Id'].isin(filter_users))]
del filter_movies, filter_users, min_movie_ratings, min_user_ratings
#del read_data #freed the ram
print('Shape User-Ratings unfiltered:\t{}'.format(read_data.shape))
print('Shape User-Ratings filtered:\t{}'.format(User_filterd.shape))

After fitering Users:	(6310368, 4)
After fitering Movies:	(6046446, 4)
Shape User-Ratings unfiltered:	(24053764, 4)
Shape User-Ratings filtered:	(6046446, 4)


In [12]:
# Get data
data = User_filterd['Rating'].value_counts().sort_index(ascending=False)

# Create trace
trace = go.Bar(x = data.index,
               text = ['{:.1f} %'.format(val) for val in (data.values / User_filterd.shape[0] * 100)],
               textposition = 'auto',
               textfont = dict(color = '#000000'),
               y = data.values,
               marker = dict(color = '#0054db'))
# Create layout
layout = dict(title = 'Distribution Of {} Netflix-Ratings'.format(User_filterd.shape[0]),
              xaxis = dict(title = 'Rating'),
              yaxis = dict(title = 'Count'))
# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [13]:
print(User_filterd.groupby('Cust_Id')['Rating'].count().sort_values(ascending=False))#num of ratings per user

Cust_Id
305344     1904
387418     1897
2439493    1858
2118461    1834
1664010    1761
           ... 
1035139     129
521985      129
907347      125
1850615     123
2048620     111
Name: Rating, Length: 21045, dtype: int64


In [14]:
##### Ratings Per User #####
# Get data
data = User_filterd.groupby('Cust_Id')['Rating'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(size = 50),
                     marker = dict(color = '#0054db'))
# Create layout
layout = go.Layout(title = 'Distribution Of Ratings Per User {} Netflix-Ratings'.format(User_filterd.shape[0]),
                   xaxis = dict(title = 'Ratings Per User'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [15]:
print(User_filterd.groupby('Movie_Id')['Rating'].count().sort_values(ascending=False))#num of ratings per movie

Movie_Id
1905    19919
4306    19841
2862    19442
2452    19101
607     18683
        ...  
2458      302
1316      302
2069      300
4293      300
4409      300
Name: Rating, Length: 1911, dtype: int64


In [16]:
##### Ratings Per Movie #####
# Get data
data = User_filterd.groupby('Movie_Id')['Rating'].count()

# Create trace
trace = go.Histogram(x = data.values,
                     name = 'Ratings',
                     xbins = dict(size = 100),
                     marker = dict(color = '#0054db'))
# Create layout
layout = go.Layout(title = 'Distribution Of Ratings Per Movie {} Netflix-Ratings'.format(User_filterd.shape[0]),
                   xaxis = dict(title = 'Ratings Per Movie'),
                   yaxis = dict(title = 'Count'),
                   bargap = 0.2)

# Create plot
fig = go.Figure(data=[trace], layout=layout)
iplot(fig)

In [17]:
from surprise import Dataset, Reader
from surprise.model_selection import train_test_split, cross_validate
from surprise.model_selection import train_test_split, cross_validate
from surprise import accuracy

reader = Reader(rating_scale=(1, 5))
data = Dataset.load_from_df(User_filterd[['Cust_Id', 'Movie_Id', 'Rating']], reader)
trainsetfull = data.build_full_trainset()

print('Number of users: ', trainsetfull.n_users, '\n')
print('Number of items: ', trainsetfull.n_items, '\n')

Number of users:  21045 

Number of items:  1911 



In [18]:
from surprise import BaselineOnly

bsl_options = {'method': 'als', 'n_epochs': 2}
als = BaselineOnly(bsl_options=bsl_options)
cross_validate(als, data, measures=['RMSE', 'MAE'], cv=3, verbose=True)

Estimating biases using als...
Estimating biases using als...
Estimating biases using als...
Evaluating RMSE, MAE of algorithm BaselineOnly on 3 split(s).

                  Fold 1  Fold 2  Fold 3  Mean    Std     
RMSE (testset)    0.9035  0.9039  0.9031  0.9035  0.0003  
MAE (testset)     0.7106  0.7111  0.7104  0.7107  0.0003  
Fit time          7.37    9.56    9.46    8.80    1.01    
Test time         35.96   28.44   31.84   32.08   3.07    


{'test_rmse': array([0.90347827, 0.90389563, 0.90311949]),
 'test_mae': array([0.71062625, 0.71106946, 0.71038057]),
 'fit_time': (7.369720935821533, 9.558865785598755, 9.464157342910767),
 'test_time': (35.95809197425842, 28.44321084022522, 31.838984966278076)}

In [19]:
from surprise import BaselineOnly

bsl_options = {'method': 'sgd', 'n_epochs': 2}
sgd = BaselineOnly(bsl_options=bsl_options)
cross_validate(sgd, data, measures=['RMSE', 'MAE'], cv=3, verbose=True)

Estimating biases using sgd...
Estimating biases using sgd...
Estimating biases using sgd...
Evaluating RMSE, MAE of algorithm BaselineOnly on 3 split(s).

                  Fold 1  Fold 2  Fold 3  Mean    Std     
RMSE (testset)    0.9072  0.9077  0.9074  0.9074  0.0002  
MAE (testset)     0.7155  0.7162  0.7158  0.7158  0.0003  
Fit time          8.33    10.27   10.06   9.55    0.87    
Test time         35.84   30.54   32.28   32.88   2.21    


{'test_rmse': array([0.90719364, 0.90770368, 0.90736631]),
 'test_mae': array([0.71546017, 0.71619283, 0.7157538 ]),
 'fit_time': (8.327446222305298, 10.273815631866455, 10.061811447143555),
 'test_time': (35.83838224411011, 30.53674340248108, 32.27849268913269)}

In [20]:
from surprise import SVD

svd = SVD(verbose=True, n_epochs=2)
cross_validate(svd, data, measures=['RMSE', 'MAE'], cv=3, verbose=True)

Processing epoch 0
Processing epoch 1
Processing epoch 0
Processing epoch 1
Processing epoch 0
Processing epoch 1
Evaluating RMSE, MAE of algorithm SVD on 3 split(s).

                  Fold 1  Fold 2  Fold 3  Mean    Std     
RMSE (testset)    0.9068  0.9070  0.9072  0.9070  0.0002  
MAE (testset)     0.7158  0.7157  0.7158  0.7158  0.0000  
Fit time          52.33   54.24   53.89   53.49   0.83    
Test time         48.81   51.38   43.57   47.92   3.25    


{'test_rmse': array([0.90682555, 0.9069895 , 0.90723994]),
 'test_mae': array([0.7158159 , 0.71573062, 0.71582972]),
 'fit_time': (52.329137325286865, 54.23896908760071, 53.892802000045776),
 'test_time': (48.8062059879303, 51.38144493103027, 43.5671820640564)}

In [21]:
from surprise import NMF

nmf = NMF(verbose=True, n_epochs=2)
cross_validate(nmf, data, measures=['RMSE', 'MAE'], cv=3, verbose=True)

Processing epoch 0
Processing epoch 1
Processing epoch 0
Processing epoch 1
Processing epoch 0
Processing epoch 1
Evaluating RMSE, MAE of algorithm NMF on 3 split(s).

                  Fold 1  Fold 2  Fold 3  Mean    Std     
RMSE (testset)    1.0355  1.0254  1.0313  1.0307  0.0041  
MAE (testset)     0.7982  0.7905  0.7949  0.7945  0.0032  
Fit time          23.65   25.50   25.64   24.93   0.91    
Test time         39.47   42.30   38.76   40.17   1.53    


{'test_rmse': array([1.03550967, 1.02542601, 1.03128727]),
 'test_mae': array([0.7981667 , 0.79047464, 0.79493613]),
 'fit_time': (23.651564121246338, 25.502363681793213, 25.63882064819336),
 'test_time': (39.46731233596802, 42.29734492301941, 38.75967025756836)}

In [22]:
als.fit(trainsetfull)
sgd.fit(trainsetfull)
svd.fit(trainsetfull)
nmf.fit(trainsetfull)

Estimating biases using als...
Estimating biases using sgd...
Processing epoch 0
Processing epoch 1
Processing epoch 0
Processing epoch 1


In [23]:
#Dataframe of unique Movie_Id
mv_list = User_filterd['Movie_Id'].unique()
mv_list = pd.DataFrame(mv_list, columns=["Movie_Id"])

def predict_rating(id, model):
    rated_mv = User_filterd.Movie_Id[(User_filterd.Cust_Id == id)].tolist()
    pred = mv_list.copy()
    pred['Estimate_Score'] = pred['Movie_Id'].apply(lambda x: model.predict(id, x).est if x not in rated_mv else np.nan)
    pred = pred.dropna()
    pred = pred.sort_values('Estimate_Score', ascending=False)
    print(pred)

In [24]:
User_filterd

Cust_Id  Rating     Date_Rt  Movie_Id
696        712664       5  2004-02-01         3
697       1331154       4  2004-07-03         3
703       1644750       3  2003-03-19         3
708        701730       2  2005-10-05         3
711        931626       2  2004-07-08         3
...           ...     ...         ...       ...
24057556  2237988       3  2004-09-03      4497
24057557  1222252       3  2004-11-08      4497
24057559  2111672       3  2003-05-03      4497
24057560   900899       3  2004-03-10      4497
24057561  1300759       3  2004-09-21      4497

[6046446 rows x 4 columns]

In [25]:
print('ASL prediction\n')
predict_rating(2162665, als)
print('SGD prediction\n')
predict_rating(2162665, sgd)
print('\nSVD prediction\n')
predict_rating(2162665, svd)
print('\nNMF prediction\n')
predict_rating(2162665, nmf)

ASL prediction

      Movie_Id  Estimate_Score
1462      3456        4.321050
884       2102        4.136360
1457      3444        4.055124
921       2172        4.021995
633       1476        4.010264
...        ...             ...
966       2276        1.745721
1867      4394        1.741894
1273      3021        1.565988
1623      3849        1.541514
1544      3667        1.476934

[1615 rows x 2 columns]
SGD prediction

      Movie_Id  Estimate_Score
1462      3456        4.268665
884       2102        4.206978
1457      3444        4.192379
921       2172        4.147393
1881      4427        4.032360
...        ...             ...
1867      4394        1.691232
1510      3573        1.670095
1623      3849        1.524865
1544      3667        1.459331
1273      3021        1.417943

[1615 rows x 2 columns]

SVD prediction

      Movie_Id  Estimate_Score
884       2102        4.255841
1462      3456        4.242916
1457      3444        4.220452
921       2172        4.211742
82